# Helper Scripts

In [18]:
# Cleaner
# flights = flights.replace('null', np.nan) # replace all null values with np.nan's
# flights['fly_score'] = flights['fly_score'].str.replace('FlyScore ', '').astype(float) # extract string of fly score then convert to float
# flights['price'] = flights['price'].str.replace('$', '').str.replace(',', '').astype(float) # convert $1,000 to 1000.0
# flights['airline'] = flights['airline'].str[11:] # extract string of airline name
# flights.dropna(subset=['price','duration'], inplace=True) # drop all rows with nulls in price or duration (191)
# flights["departure_date"] = flights['departure_date'].apply(lambda x: pd.to_datetime(str(x), format='%Y%m%d')) # convert integer to datetime
# flights.duration = flights.duration.str.replace('h', '').str.replace(' ', '+').str.replace('m', '/60').apply(eval).round(2) # convert Xh Ym to hours in decimal
# flights.set_index(pd.Series(range(len(flights.price))), inplace=True) # set index to 1 thru 91564

# flights2 = flights.copy() # make new copy of master dataframe
# flights2 = flights2.set_index('departure_date') # set departure date as datetime index
# flights2['Weekday Name'] = flights2.index.weekday_name # make new column called weekday name based on datetime

In [ ]:
# flights['month'] = pd.DatetimeIndex(flights.departure_date).month
# flights['day'] = pd.DatetimeIndex(flights.departure_date).day
# flights['depart_time'] = flights.start_end_time.apply(lambda x: x.split(' - ')[0])
# flights['arrival_time'] = flights.start_end_time.apply(lambda x: x.split(' - ')[1])
# flights['mo_name'] = pd.to_datetime(flights['month'], format='%m').dt.month_name().str.slice(stop=3)
# flights['overnight'] = flights.arrival_time.apply(lambda x:  if (x[-2:] == '+1') else 0)
# flights.arrival_time = flights.arrival_time.apply(lambda x: x[0:len(x)-2] if (x[-2:] == '+1') else x)
# flights['arrival_date'] = pd.to_datetime(flights.departure_date)
# flights.departure_date = pd.to_datetime(flights.departure_date)
# flights.loc[flights.overnight > 0, 'arrival_date'] = flights.arrival_date + timedelta(days=1)
# flights = flights.drop(columns=['start_end_time'])
# cols = flights.columns.tolist()
# cols = [cols[0], cols[10], cols[3], cols[14], cols[11], cols[4], cols[5], cols[13], cols[2], cols[1], cols[6], cols[7], cols[9], cols[12], cols[8]]
# flights = flights[cols]

In [ ]:
# Python program to convert time 
# from 12 hour to 24 hour format 
  
# Function to convert the date format 
def convert24(str1): 
      
    # Checking if last two elements of time 
    # is AM and first two elements are 12 
    if str1[-2:] == "AM" and str1[:2] == "12": 
        return "00" + str1[2:len(str1)-3] + ':00'
          
    # remove the AM     
    elif str1[-2:] == "AM" and str1[1] != ':': 
        return str1[:-3] + ':00'
    
    elif str1[-2:] == "AM" and str1[1] == ':':
        return "0" + str1[:-3] + ':00'
      
    # Checking if last two elements of time 
    # is PM and first two elements are 12    
    elif str1[-2:] == "PM" and str1[:2] == "12": 
        return str1[:len(str1)-3] + ':00'
    
    elif str1[-2:] == "PM" and str1[1] != ':':
        return str(int(str1[:2]) + 12) + str1[2:len(str1)-3] + ':00'
    
    elif str1[-2:] == "PM" and str1[1] == ':':
        return str(int(str1[:1]) + 12) + str1[1:len(str1)-3] + ':00'
          
    else: 
        return str1

# Driver code
convert24("5:31 AM")

In [30]:
# flights.depart_time = flights.depart_time.apply(lambda x: convert24(x))
# flights.arrival_time = flights.arrival_time.apply(lambda x: convert24(x))

In [24]:
flights.to_csv('all_flights_new.csv')

# Import Data

In [1]:
import numpy as np
import pandas as pd
import sklearn
import re
import datetime as dt
import time

In [2]:
flights = pd.read_csv('all_flights_minus_LHR.csv', index_col=[0])
# flights = pd.read_csv('all_flights_new.csv', index_col=[0])

flights.departure_date = pd.to_datetime(flights.departure_date)
flights.arrival_date = pd.to_datetime(flights.arrival_date)
flights.depart_time = pd.to_timedelta(flights.depart_time)
flights.arrival_time = pd.to_timedelta(flights.arrival_time)

In [3]:
flights

departure_date depart_time origin arrival_date arrival_time destination  \
0         2020-01-28    08:30:00    EWR   2020-01-28     11:50:00         LAX   
1         2020-01-28    11:00:00    EWR   2020-01-28     14:28:00         LAX   
2         2020-01-28    17:00:00    EWR   2020-01-28     20:28:00         LAX   
3         2020-01-28    19:00:00    EWR   2020-01-28     22:28:00         LAX   
4         2020-01-28    18:00:00    EWR   2020-01-28     21:29:00         LAX   
...              ...         ...    ...          ...          ...         ...   
89641     2020-12-07    15:45:00    LGA   2020-12-07     17:10:00         YUL   
89642     2020-12-07    17:40:00    LGA   2020-12-07     19:05:00         YUL   
89643     2020-12-07    14:41:00    EWR   2020-12-07     16:15:00         YUL   
89644     2020-12-07    12:13:00    EWR   2020-12-07     13:48:00         YUL   
89645     2020-12-07    19:59:00    EWR   2020-12-07     21:39:00         YUL   

       duration  overnight airline  price  fly_score day_of_week  day mo_name  \
0          6.33          0  United  354.0        5.9     Tuesday   28     Jan   
1          6.47          0  United  354.0        7.9     Tuesday   28     Jan   
2          6.47          0  United  354.0        7.9     Tuesday   28     Jan   
3          6.47          0  United  354.0        7.9     Tuesday   28     Jan   
4          6.48          0  United  354.0        7.9     Tuesday   28     Jan   
...         ...        ...     ...    ...        ...         ...  ...     ...   
89641      1.42          0  United  203.0        5.9      Monday    7     Dec   
89642      1.42          0  United  203.0        5.9      Monday    7     Dec   
89643      1.57          0  United  782.0        5.2      Monday    7     Dec   
89644      1.58          0  United  782.0        5.2      Monday    7     Dec   
89645      1.67          0  United  782.0        5.2      Monday    7     Dec   

       month  
0          1  
1          1  
2          1  
3          1  
4          1  
...      ...  
89641     12  
89642     12  
89643     12  
89644     12  
89645     12  

[57801 rows x 15 columns]

In [4]:
flights.dtypes

departure_date     datetime64[ns]
depart_time       timedelta64[ns]
origin                     object
arrival_date       datetime64[ns]
arrival_time      timedelta64[ns]
destination                object
duration                  float64
overnight                   int64
airline                    object
price                     float64
fly_score                 float64
day_of_week                object
day                         int64
mo_name                    object
month                       int64
dtype: object

# EDA

In [5]:
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns

In [6]:
# Airlines represented in the data
flights.airline.unique()

array(['United', 'Alaska', 'JetBlue', 'American', 'Spirit', 'Frontier',
       'Air Canada', 'WestJet'], dtype=object)

In [7]:
# The 5 destinations, 3 domestic (LA, Chicago, Miami) and 2 close intl (San Juan, Montreal)
flights.destination.unique()

array(['LAX', 'ORD', 'MIA', 'SJU', 'YUL'], dtype=object)

In [180]:
flights.query("price <= 500 and destination == 'MIA'")

departure_date depart_time origin arrival_date arrival_time destination  \
33        2020-01-28    06:00:00    EWR   2020-01-28     09:18:00         MIA   
34        2020-01-28    14:30:00    EWR   2020-01-28     17:37:00         MIA   
35        2020-01-28    20:29:00    EWR   2020-01-28     23:40:00         MIA   
36        2020-01-28    21:00:00    EWR   2020-01-29     00:12:00         MIA   
37        2020-01-28    17:00:00    EWR   2020-01-28     20:15:00         MIA   
...              ...         ...    ...          ...          ...         ...   
89589     2020-12-07    06:15:00    EWR   2020-12-07     09:19:00         MIA   
89590     2020-12-07    13:20:00    EWR   2020-12-07     16:27:00         MIA   
89591     2020-12-07    14:29:00    EWR   2020-12-07     17:34:00         MIA   
89592     2020-12-07    09:00:00    EWR   2020-12-07     12:08:00         MIA   
89593     2020-12-07    07:30:00    EWR   2020-12-07     10:34:00         MIA   

       duration  overnight   airline  price  fly_score day_of_week  day  \
33         3.30          0  Frontier   49.0        6.3     Tuesday   28   
34         3.12          0    United   87.0        7.1     Tuesday   28   
35         3.18          0    United   87.0        7.6     Tuesday   28   
36         3.20          1    United   87.0        7.6     Tuesday   28   
37         3.25          0    United   87.0        7.1     Tuesday   28   
...         ...        ...       ...    ...        ...         ...  ...   
89589      3.07          0  American  139.0        6.4      Monday    7   
89590      3.12          0  American  139.0        6.4      Monday    7   
89591      3.08          0    United  189.0        7.6      Monday    7   
89592      3.13          0    United  189.0        7.6      Monday    7   
89593      3.07          0    United  239.0        7.6      Monday    7   

      mo_name  month  
33        Jan      1  
34        Jan      1  
35        Jan      1  
36        Jan      1  
37        Jan      1  
...       ...    ...  
89589     Dec     12  
89590     Dec     12  
89591     Dec     12  
89592     Dec     12  
89593     Dec     12  

[11906 rows x 15 columns]

## Boxplot of the 8 airlines and the distribution of prices

In [187]:
fig1 = go.Figure()

fig1 = fig1.add_trace(go.Box(
    y = flights.query("price <= 500 and destination == 'LAX'").price,
    x = flights.query("price <= 500 and destination == 'LAX'").airline,
    marker_color = '#3D9970'
))

fig1 = fig1.update_layout(
    title={
        'text': "Distribution of Flight Prices by Airline From NYC to LAX",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis = dict(
        title = "",
        categoryorder = 'array',
        categoryarray = ['Frontier', 'American', 'Alaska', 'United', 'JetBlue', 'Spirit', 'WestJet']
    ),
    yaxis = dict(
        title = "Flight Prices (USD)",
        tickmode = 'linear',
        tick0 = 0,
        dtick = 50,
        tickprefix = '$'
    ),
    font = dict(
        family = "Verdana, monospace",
        size = 14,
        color = "#7f7f7f"
    )
)

In [188]:
fig1.show()

## Time Series of Avg Daily Prices
### By 1 week, 1 month, 3 months, 6 months, 9 months, and all (~10.5 months)

In [154]:
flights1 = flights.copy()

In [155]:
flights1 = flights1.groupby('departure_date').agg({'price': 'mean'}).reset_index()

In [156]:
fig2 = go.Figure(go.Scatter(x = flights1["departure_date"], y = round(flights1["price"], 2)))

fig2.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=7, label="1w", step="day", stepmode="backward"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=9, label="9m", step="month", stepmode="backward"),
            dict(label = "All", step="all")
        ])
    )
)

fig2.update_layout(
    title={
        'text': "Average Daily Flight Prices Departing NYC Airports",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis_title="Time Series Date Range (01/27/20 - 12/21/20)",
    yaxis = dict(
        title = "Average Daily Price (USD)",
        tickmode = 'linear',
        tick0 = 50,
        dtick = 50,
        tickprefix = '$'
    ),
    font = dict(
        family="Verdana, monospace",
        size=14,
        color="#7f7f7f"
    )
)

## Boxplot of Fly Scores based on Day of the Week

In [139]:
fig3 = go.Figure()

fig3 = fig3.add_trace(go.Box(
    y = flights.fly_score,
    x = flights.day_of_week,
    marker_color = '#FF851B'
))

fig3 = fig3.update_layout(
    title={
        'text': "Distribution of Airline Fly Scores by Day of the Week",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis = dict(
        title = "",
        categoryorder = 'array',
        categoryarray = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
    ),
    yaxis = dict(
        title = "Fly Score (0 to 10)",
        tickmode = 'linear',
        tick0 = 5,
        dtick = 0.5
    ),
    font = dict(
        family = "Verdana, monospace",
        size = 14,
        color = "#7f7f7f"
    )
)

In [140]:
fig3.show()

## Boxplot of Prices based on Day of the Week

In [161]:
fig4 = go.Figure()

fig4 = fig4.add_trace(go.Box(
    y = flights[flights.price <= 500].price,
    x = flights[flights.price <= 500].day_of_week,
    marker_color = 'indianred'
))

fig4 = fig4.update_layout(
    title={
        'text': "Distribution of Flight Prices by Day of the Week",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis = dict(
        title = "",
        categoryorder = 'array',
        categoryarray = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
    ),
    yaxis = dict(
        title = "Flight Price (USD)",
        tickmode = 'linear',
        tick0 = 0,
        dtick = 50,
        tickprefix = '$'
    ),
    font = dict(
        family = "Verdana, monospace",
        size = 14,
        color = "#7f7f7f"
    )
)

In [162]:
fig4.show()

## Average Monthly Prices as Bar Chart

In [24]:
flights2 = flights.copy()

In [25]:
flights2 = flights2[flights2.mo_name != 'Jan'].groupby('mo_name').agg({'price': 'mean'}).reset_index()

In [79]:
# Average monthly prices
colors = ['rgb(26, 118, 255)',] * 11
colors[10] = 'LightSeaGreen'
colors[5] = 'crimson'

fig5 = go.Figure(go.Bar(x = flights2["mo_name"], y = round(flights2["price"], 2), marker_color = colors))

fig5.update_layout(
    title={
        'text': "Average Monthly Flight Prices Departing NYC in 2020",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis = dict(
        title = "",
        categoryorder = 'array',
        categoryarray = ['Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
    ),
    yaxis = dict(
        title = "Average Monthly Price (USD)",
        tickmode = 'linear',
        tick0 = 0,
        dtick = 25,
        tickprefix = '$'
    ),
    font = dict(
        family = "Verdana, monospace",
        size = 14,
        color = "#7f7f7f"
    ),
    shapes = [
        dict(
            type = "line",
            x0 = 'Feb',
            y0 = 182.08,
            x1 = 'Dec',
            y1 = 182.08,
            name = 'Average',
            line = dict(
                color="MediumPurple",
                width=3,
                dash="dash")
        )
    ]
)

fig5.show()

In [35]:
flights2.price.mean()

182.07665075277933